In [1]:
import os
import sys
import os.path
import glob
import numpy as np
import pandas as pd
import subprocess
import matplotlib.pyplot as plt
import numpy as np
import seaborn as sns

## Read the training set

In [44]:
# read the training set (you'll obviously need to change the path here)
TrainingSet = pd.read_csv("/data/critt/shared/devin/LS14_Training_Set_DG.csv")

print("Training set words, features:", TrainingSet.shape)
TrainingSet.head()

Training set words, features: (28828, 19)


TDIbin   TDIcont  Text  Id   SToken       TGroup  PoS CAT   Prob1   Prob2  \
0       0  0.971240     1   1   Rather  En_lugar_de   RB   R -3.7787  0.0000   
1       0  0.000000     1   2     than  En_lugar_de   IN   I -3.0880 -6.3203   
2       1  0.394742     1   3    being  inquietarse  VBG   V -3.1516 -5.9298   
3       1  0.394742     1   4  rattled  inquietarse  VBN   V -5.5136 -7.7901   
4       0  0.000000     1   5       by          por   IN   I -2.3879 -7.0120   

    AERmean   I_NTOtg   H_NTOtg   I_NTOsg   H_NTOsg   I_NTOcs   H_NTOcs  \
0  0.533333  2.237039  0.930822  0.044394  0.195909  0.044394  0.195909   
1  0.000000  0.044394  0.195909  0.044394  0.195909  2.237039  0.930822   
2  0.066667  0.520832  1.603434  0.137504  0.583584  0.137504  0.583584   
3  0.166667  4.044394  1.983983  0.289507  1.009944  0.343954  1.196930   
4  0.000000  0.044394  0.195909  0.044394  0.195909  0.343954  1.280411   

   I_NTOstc  H_NTOstc  
0  2.237039  0.930822  
1  2.237039  0.930822  
2  0.520832  1.603434  
3  4.044394  1.983983  
4  0.343954  1.280411

# Explanation of features
## Entire data set is from CRITT TPR-DB study "LS14"
### Many of the feature explanations below will only really make sense in the context of Devin Gilbert's dissertation, "Directing Post-Editors’ Attention to Machine Translation Output that Needs Editing through an Enhanced User Interface: Viability and Automatic Application via a Word-level Translation Accuracy Indicator"
- TDIbin is the label. "1" is "Difficult" and "0" is "Easy"
- TDIcont is an attempt at making a continuous variable for the label (closer to "1" is more "difficult")
- Text is text number in LS14 study
- Id is the word's index within each text
- SToken is the ST word
- TGroup is the Target Alignment Group
- PoS is the automatically generated part-of-speech tags
- CAT is the word class (derived from PoS)
- Prob1 is unigram log10 frequency according to the British National Corpus
- Prob2 is bigram log10 frequency according to the British National Corpus
- AERmean is a misnomer and is actually average WADI score
- For the rest of the features,
    - "I" stands for shannon information;
    - "H" stands for shannon information entropy,
    - "NTO" stands for "Intento", meaning that the feature was generated from ten different MT outputs of the STs in the LS14 study (obtained from integrating with Intento's API);
    - "tg" stands for "target alignment group," meaning the information or entropy value was calculated for the SToken using the target alignment group;
    - "sg" stands for "source alignment group," meaning the information or entropy value was calculated for the SToken using the source alignment group;
    - "cs" stands for "Cross value," meaning the information or entropy value was calculated for the SToken using the Cross value;
    - "stc" stands for "source, target, cross," meaning the information or entropy value was calculated for the SToken using a concatenation of the source alignment group, the target alignment group, and the Cross value.

### For explanations of the PoS tagging process (p. 27); the calculation of Cross (pp. 26-27), Information, and Entropy values (pp. 29–33); and the generation of Prob1 and Prob2 (p. 27), see Carl, Michael; Schaeffer, Moritz; Bangalore, Srinivas (2016). "The CRITT Translation Process Research Database" in New Directions in Empirical Translation Process Research. Springer. (pp. 13–54) 

## Data Preprocessing

In [45]:
# Import LabelEncoder
import sklearn
from sklearn import preprocessing

#creating labelEncoder
le = preprocessing.LabelEncoder()

# Converting string labels of categories (word class) into numbers.
cat = TrainingSet['CAT']
cat_encoded=le.fit_transform(cat)

TrainingSet['CATnum'] = cat_encoded

# Let's make some windows and non-linear transformations (to generate new features)

## Run Function "generate_features_from_features"

In [34]:
pd.set_option('display.max_columns', None)

# Choose which features to create new features for
selectFeatures = [
    'I_NTOcs',
    'CATnum',
    'I_NTOtg'
]

# Run function, change value of "howFar" to decide size of context windows
TrainingSet = generate_features_from_features(TrainingSet, selectFeatures, howFar=2)
TrainingSet.head()

TDIbin   TDIcont  Text  Id   SToken       TGroup  PoS CAT   Prob1   Prob2  \
0       0  0.971240     1   1   Rather  En_lugar_de   RB   R -3.7787  0.0000   
1       0  0.000000     1   2     than  En_lugar_de   IN   I -3.0880 -6.3203   
2       1  0.394742     1   3    being  inquietarse  VBG   V -3.1516 -5.9298   
3       1  0.394742     1   4  rattled  inquietarse  VBN   V -5.5136 -7.7901   
4       0  0.000000     1   5       by          por   IN   I -2.3879 -7.0120   

    AERmean   I_NTOtg   H_NTOtg   I_NTOsg   H_NTOsg   I_NTOcs   H_NTOcs  \
0  0.533333  2.237039  0.930822  0.044394  0.195909  0.044394  0.195909   
1  0.000000  0.044394  0.195909  0.044394  0.195909  2.237039  0.930822   
2  0.066667  0.520832  1.603434  0.137504  0.583584  0.137504  0.583584   
3  0.166667  4.044394  1.983983  0.289507  1.009944  0.343954  1.196930   
4  0.000000  0.044394  0.195909  0.044394  0.195909  0.343954  1.280411   

   I_NTOstc  H_NTOstc  CATnum  log_I_NTOcs  L1_I_NTOcs  log_L1_I_NTOcs  \
0  2.237039  0.930822      15     0.715101   -1.000000        0.000000   
1  2.237039  0.930822       9     1.443865    0.044394        0.715101   
2  0.520832  1.603434      17     0.759639    2.237039        1.443865   
3  4.044394  1.983983      17     0.851839    0.137504        0.759639   
4  0.343954  1.280411       9     0.851839    0.343954        0.851839   

   R1_I_NTOcs  log_R1_I_NTOcs  L2_I_NTOcs  log_L2_I_NTOcs  R2_I_NTOcs  \
0    2.237039        1.443865   -1.000000        0.000000    0.137504   
1    0.137504        0.759639   -1.000000        0.000000    0.343954   
2    0.343954        0.851839    0.044394        0.715101    0.343954   
3    0.343954        0.851839    2.237039        1.443865    0.090198   
4    0.090198        0.737259    0.137504        0.759639    3.459432   

   log_R2_I_NTOcs  W5_I_NTOcs  log_W5_I_NTOcs  log_CATnum  L1_CATnum  \
0        0.759639    0.374543        2.203503    2.833213         -1   
1        0.851839   -0.474148        2.326579    2.397895         15   
2        0.851839    2.969342        3.862645    2.944439          9   
3        0.737259    2.808695        3.792601    2.944439         17   
4        1.697345    4.031087        4.046081    2.397895         17   

   log_L1_CATnum  R1_CATnum  log_R1_CATnum  L2_CATnum  log_L2_CATnum  \
0       0.000000          9       2.397895         -1       0.000000   
1       2.833213         17       2.944439         -1       0.000000   
2       2.397895         17       2.944439         15       2.833213   
3       2.944439          9       2.397895          9       2.397895   
4       2.944439          7       2.197225         17       2.944439   

   R2_CATnum  log_R2_CATnum  W5_CATnum  log_W5_CATnum  log_I_NTOtg  \
0         17       2.944439         24       5.342334     1.443865   
1         17       2.944439         48       8.722091     0.715101   
2          9       2.397895         50      10.573443     0.924589   
3          7       2.197225         42       9.937454     1.799131   
4         13       2.708050         54      10.794153     0.715101   

   L1_I_NTOtg  log_L1_I_NTOtg  R1_I_NTOtg  log_R1_I_NTOtg  L2_I_NTOtg  \
0   -1.000000        0.000000    0.044394        0.715101   -1.000000   
1    2.237039        1.443865    0.520832        0.924589   -1.000000   
2    0.044394        0.715101    4.044394        1.799131    2.237039   
3    0.520832        0.924589    0.044394        0.715101    0.044394   
4    4.044394        1.799131    0.090198        0.737259    0.520832   

   log_L2_I_NTOtg  R2_I_NTOtg  log_R2_I_NTOtg  W5_I_NTOtg  log_W5_I_NTOtg  
0        0.000000    0.520832        0.924589   -1.434774        1.639691  
1        0.000000    4.044394        1.799131    5.802265        4.167585  
2        1.443865    0.044394        0.715101    6.370222        4.673199  
3        0.715101    0.090198        0.737259    0.699818        3.092051  
4        0.924589    3.459432        1.697345    8.114856        5.158324

## Create training data and test data
### Change the code here to select which features you will include in the training and test data

In [46]:
Y = TrainingSet['TDIbin']

# Change the code here to select which features you will include in the training and test data
X = TrainingSet[:][['CATnum', 'I_NTOtg', 'H_NTOtg']] 
#X = TrainingSet.iloc[:,8:-1] # selects all

# Naive Bayes in a Loop

In [41]:
# X ; Y ; % of set that should be for testing ; iterations
result_NB = NB_loop(X, Y, .1, 1)
result_NB

              precision    recall  f1-score   support

        Easy       0.92      0.83      0.87      2552
   Difficult       0.24      0.43      0.31       331

    accuracy                           0.78      2883
   macro avg       0.58      0.63      0.59      2883
weighted avg       0.84      0.78      0.81      2883



# Random Forest in a Loop

In [47]:
# X ; Y ; % of set that should be for testing ; iterations ; number of decision trees
result_RF = RF_loop(X, Y, .1, 1, 600)
result_RF

              precision    recall  f1-score   support

        Easy       0.90      0.96      0.93      2554
   Difficult       0.39      0.19      0.26       329

    accuracy                           0.87      2883
   macro avg       0.65      0.58      0.59      2883
weighted avg       0.84      0.87      0.85      2883



# SVM in a Loop

In [48]:
# X ; Y ; % of set that should be for testing ; iterations
result_SVM = SVM_loop(X, Y, .1, 1)
result_SVM

              precision    recall  f1-score   support

        Easy       0.88      1.00      0.94      2540
   Difficult       0.00      0.00      0.00       343

    accuracy                           0.88      2883
   macro avg       0.44      0.50      0.47      2883
weighted avg       0.78      0.88      0.83      2883



/usr/local/lib64/python3.6/site-packages/sklearn/metrics/_classification.py:1221: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


# Experiment with Neural Classifier
### All this from (https://www.pluralsight.com/guides/machine-learning-neural-networks-scikit-learn)

In [15]:
import matplotlib.pyplot as plt
import sklearn
from sklearn.neural_network import MLPClassifier
from sklearn.neural_network import MLPRegressor

# Import necessary modules
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
from math import sqrt
from sklearn.metrics import r2_score

In [25]:
# Eliminate extraneous columns
TrainingSetTrimmed = TrainingSet.drop(columns=['TDIcont', 'Text', 'Id', 'SToken', 'TGroup', 'CAT', 'PoS', 'Prob2'])

In [26]:
TrainingSetTrimmed.describe().transpose()

count       mean       std        min        25%        50%  \
TDIbin          28828.0   0.109581  0.312372   0.000000   0.000000   0.000000   
Prob1           28828.0  -4.800517  8.186101 -50.000000  -4.499025  -3.387500   
AERmean         28828.0   0.233039  0.383918   0.000000   0.000000   0.033333   
I_NTOtg         28828.0   1.261613  1.567823   0.000000   0.044394   0.343954   
H_NTOtg         28828.0   1.012879  0.764135   0.000000   0.195909   0.871024   
I_NTOsg         28828.0   0.576855  1.055898   0.000000   0.044394   0.090198   
H_NTOsg         28828.0   0.615260  0.557049   0.000000   0.195909   0.329846   
I_NTOcs         28828.0   1.309304  1.515881   0.000000   0.137504   0.584963   
H_NTOcs         28828.0   1.117553  0.734251   0.000000   0.522978   1.052842   
I_NTOstc        28828.0   1.908865  1.772288   0.000000   0.237039   1.237039   
H_NTOstc        28828.0   1.477058  0.897569   0.000000   0.714653   1.421701   
CATnum          28828.0  11.224851  4.287094   0.000000   7.000000  13.000000   
log_H_NTOtg     28828.0   1.072608  0.243039   0.693147   0.786596   1.054669   
L1_H_NTOtg      28828.0   1.012838  0.764212  -1.000000   0.195909   0.871024   
log_L1_H_NTOtg  28828.0   1.072581  0.243115   0.000000   0.786596   1.054669   
R1_H_NTOtg      28828.0   1.012812  0.764227  -1.000000   0.195909   0.871024   
log_R1_H_NTOtg  28828.0   1.072571  0.243121   0.000000   0.786596   1.054669   
W3_H_NTOtg      28828.0   2.025650  1.156842  -0.804091   1.145247   1.903655   
log_W3_H_NTOtg  28828.0   2.145152  0.368384   0.786596   1.868177   2.124963   
log_CATnum      28828.0   2.513895  0.399523   0.693147   2.197225   2.708050   
L1_CATnum       28828.0  11.224677  4.287488  -1.000000   7.000000  13.000000   
log_L1_CATnum   28828.0   2.513833  0.399775   0.000000   2.197225   2.708050   
R1_CATnum       28828.0  11.224296  4.287641  -1.000000   7.000000  13.000000   
log_R1_CATnum   28828.0   2.513797  0.399793   0.000000   2.197225   2.708050   
W3_CATnum       28828.0  22.448973  6.080039   2.000000  19.000000  22.000000   
log_W3_CATnum   28828.0   5.027629  0.565861   2.079442   4.736198   5.105945   
log_I_NTOtg     28828.0   1.085888  0.418948   0.693147   0.715101   0.851839   
L1_I_NTOtg      28828.0   1.261577  1.567863  -1.000000   0.044394   0.343954   
log_L1_I_NTOtg  28828.0   1.085863  0.418991   0.000000   0.715101   0.851839   
R1_I_NTOtg      28828.0   1.261501  1.567869  -1.000000   0.044394   0.343954   
log_R1_I_NTOtg  28828.0   1.085838  0.418991   0.000000   0.715101   0.851839   
W3_I_NTOtg      28828.0   2.523077  2.312260  -0.955606   0.423452   1.831400   
log_W3_I_NTOtg  28828.0   2.171701  0.618094   0.715101   1.587416   2.092944   

                      75%        max  
TDIbin           0.000000   1.000000  
Prob1           -2.097000  -1.309600  
AERmean          0.366667   3.800000  
I_NTOtg          2.044394   5.044394  
H_NTOtg          1.553684   4.233640  
I_NTOsg          0.584963   5.044394  
H_NTOsg          0.949338   3.654264  
I_NTOcs          2.044394   5.044394  
H_NTOcs          1.655537   3.672845  
I_NTOstc         4.044394   5.044394  
H_NTOstc         2.128849   4.574401  
CATnum          14.000000  18.000000  
log_H_NTOtg      1.267985   1.829960  
L1_H_NTOtg       1.553684   4.233640  
log_L1_H_NTOtg   1.267985   1.829960  
R1_H_NTOtg       1.553684   4.233640  
log_R1_H_NTOtg   1.267985   1.829960  
W3_H_NTOtg       2.779982   7.648506  
log_W3_H_NTOtg   2.401633   3.524061  
log_CATnum       2.772589   2.995732  
L1_CATnum       14.000000  18.000000  
log_L1_CATnum    2.772589   2.995732  
R1_CATnum       14.000000  18.000000  
log_R1_CATnum    2.772589   2.995732  
W3_CATnum       27.000000  36.000000  
log_W3_CATnum    5.429346   5.991465  
log_I_NTOtg      1.397332   1.952232  
L1_I_NTOtg       2.044394   5.044394  
log_L1_I_NTOtg   1.397332   1.952232  
R1_I_NTOtg       2.044394   5.044394  
log_R1_I_NTOtg   1.397332   1.952232  
W3_I_NTOtg     

## Set what is the label and what are the features

In [27]:
# Set label
target_column = ['TDIbin']

# Set predictor features
predictors = list(set(list(TrainingSetTrimmed.columns))-set(target_column))
# This will normalize the features
TrainingSetTrimmed[predictors] = TrainingSetTrimmed[predictors]/TrainingSetTrimmed[predictors].max()


TrainingSetTrimmed.describe().transpose()

count      mean       std       min       25%       50%  \
TDIbin          28828.0  0.109581  0.312372  0.000000  0.000000  0.000000   
Prob1           28828.0  3.665636  6.250841  1.000000  1.601252  2.586668   
AERmean         28828.0  0.061326  0.101031  0.000000  0.000000  0.008772   
I_NTOtg         28828.0  0.250102  0.310805  0.000000  0.008801  0.068185   
H_NTOtg         28828.0  0.239246  0.180491  0.000000  0.046274  0.205739   
I_NTOsg         28828.0  0.114356  0.209321  0.000000  0.008801  0.017881   
H_NTOsg         28828.0  0.168368  0.152438  0.000000  0.053611  0.090263   
I_NTOcs         28828.0  0.259556  0.300508  0.000000  0.027259  0.115963   
H_NTOcs         28828.0  0.304274  0.199913  0.000000  0.142391  0.286656   
I_NTOstc        28828.0  0.378413  0.351338  0.000000  0.046991  0.245230   
H_NTOstc        28828.0  0.322897  0.196216  0.000000  0.156229  0.310795   
CATnum          28828.0  0.623603  0.238172  0.000000  0.388889  0.722222   
log_H_NTOtg     28828.0  0.586137  0.132811  0.378777  0.429843  0.576334   
L1_H_NTOtg      28828.0  0.239236  0.180509 -0.236203  0.046274  0.205739   
log_L1_H_NTOtg  28828.0  0.586123  0.132853  0.000000  0.429843  0.576334   
R1_H_NTOtg      28828.0  0.239230  0.180513 -0.236203  0.046274  0.205739   
log_R1_H_NTOtg  28828.0  0.586117  0.132856  0.000000  0.429843  0.576334   
W3_H_NTOtg      28828.0  0.264843  0.151251 -0.105130  0.149735  0.248892   
log_W3_H_NTOtg  28828.0  0.608716  0.104534  0.223207  0.530120  0.602987   
log_CATnum      28828.0  0.839159  0.133364  0.231378  0.733452  0.903969   
L1_CATnum       28828.0  0.623593  0.238194 -0.055556  0.388889  0.722222   
log_L1_CATnum   28828.0  0.839138  0.133448  0.000000  0.733452  0.903969   
R1_CATnum       28828.0  0.623572  0.238202 -0.055556  0.388889  0.722222   
log_R1_CATnum   28828.0  0.839126  0.133454  0.000000  0.733452  0.903969   
W3_CATnum       28828.0  0.623583  0.168890  0.055556  0.527778  0.611111   
log_W3_CATnum   28828.0  0.839132  0.094445  0.347067  0.790491  0.852203   
log_I_NTOtg     28828.0  0.556229  0.214599  0.355054  0.366299  0.436341   
L1_I_NTOtg      28828.0  0.250095  0.310813 -0.198240  0.008801  0.068185   
log_L1_I_NTOtg  28828.0  0.556216  0.214621  0.000000  0.366299  0.436341   
R1_I_NTOtg      28828.0  0.250080  0.310814 -0.198240  0.008801  0.068185   
log_R1_I_NTOtg  28828.0  0.556203  0.214622  0.000000  0.366299  0.436341   
W3_I_NTOtg      28828.0  0.250087  0.229191 -0.094720  0.041973  0.181528   
log_W3_I_NTOtg  28828.0  0.556210  0.158305  0.183150  0.406564  0.536039   

                     75%        max  
TDIbin          0.000000   1.000000  
Prob1           3.435419  38.179597  
AERmean         0.096491   1.000000  
I_NTOtg         0.405280   1.000000  
H_NTOtg         0.366985   1.000000  
I_NTOsg         0.115963   1.000000  
H_NTOsg         0.259789   1.000000  
I_NTOcs         0.405280   1.000000  
H_NTOcs         0.450751   1.000000  
I_NTOstc        0.801760   1.000000  
H_NTOstc        0.465383   1.000000  
CATnum          0.777778   1.000000  
log_H_NTOtg     0.692903   1.000000  
L1_H_NTOtg      0.366985   1.000000  
log_L1_H_NTOtg  0.692903   1.000000  
R1_H_NTOtg      0.366985   1.000000  
log_R1_H_NTOtg  0.692903   1.000000  
W3_H_NTOtg      0.363467   1.000000  
log_W3_H_NTOtg  0.681496   1.000000  
log_CATnum      0.925513   1.000000  
L1_CATnum       0.777778   1.000000  
log_L1_CATnum   0.925513   1.000000  
R1_CATnum       0.777778   1.000000  
log_R1_CATnum   0.925513   1.000000  
W3_CATnum       0.750000   1.000000  
log_W3_CATnum   0.906180   1.000000  
log_I_NTOtg     0.715761   1.000000  
L1_I_NTOtg      0.405280   1.000000  
log_L1_I_NTOtg  0.715761   1.000000  
R1_I_NTOtg      0.405280   1.000000  
log_R1_I_NTOtg  0.715761   1.000000  
W3_I_NTOtg      0.405280   1.000000  
log_W3_I_NTOtg  0.661139   1.000000

## Create training and test datasets

In [28]:
XX = TrainingSetTrimmed[predictors].values
yy = TrainingSetTrimmed[target_column].values

X_train, X_test, y_train, y_test = train_test_split(XX, yy, test_size=0.30, random_state=40)
print(X_train.shape); print(X_test.shape)

(20179, 32)
(8649, 32)


## Building, predicting, and evaluating the Neural Network Model

In [29]:
from sklearn.neural_network import MLPClassifier

mlp = MLPClassifier(hidden_layer_sizes=(8,8,8), activation='relu', solver='adam', max_iter=500)
mlp.fit(X_train,y_train)

predict_train = mlp.predict(X_train)
predict_test = mlp.predict(X_test)

/usr/local/lib64/python3.6/site-packages/sklearn/utils/validation.py:73: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(**kwargs)


### Evaluate performance of model on training data

In [30]:
from sklearn.metrics import classification_report,confusion_matrix
print(confusion_matrix(y_train,predict_train))
print(classification_report(y_train,predict_train))

[[17670   303]
 [ 1814   392]]
              precision    recall  f1-score   support

           0       0.91      0.98      0.94     17973
           1       0.56      0.18      0.27      2206

    accuracy                           0.90     20179
   macro avg       0.74      0.58      0.61     20179
weighted avg       0.87      0.90      0.87     20179



### Evaluate performance of model on TEST data

In [31]:
print(confusion_matrix(y_test,predict_test))
print(classification_report(y_test,predict_test))

[[7573  123]
 [ 779  174]]
              precision    recall  f1-score   support

           0       0.91      0.98      0.94      7696
           1       0.59      0.18      0.28       953

    accuracy                           0.90      8649
   macro avg       0.75      0.58      0.61      8649
weighted avg       0.87      0.90      0.87      8649



# Functions

In [10]:
import pandas as pd

# # # Function for generating context values in a new column (values coming before and after the value you're looking at)
# # # #### Function will return a pandas Series
# -- df should be dataframe where your feature is located
# -- feature should be a string corresponding to column name from which you want to generate new feature
# -- contextDirection should be a string, either "left" or "right"
# -- contextDistance should be an integer for how many tokens away you want to gather context
def context_generator(df, feature, contextDirection, contextDistance):
    
    # make contextDistance negative if contextDirection is right (so that series will be shifted in the correct direction)
    if contextDirection == "right":
        contextDistance = -abs(contextDistance)
        
    #-------------------------------------------------
    # Here we shift values by a user's specified amount
    tempSeries = df[feature].shift(contextDistance)
    
    
    # Here we make sure the output doesn't have any NaNs, replacing it with a unique value
    tempSeries.fillna(-1, inplace=True)
    
    # if original feature was an integer, convert derivative feature to integer
    if df[feature].dtype == 'int64':
        tempSeries = tempSeries.astype(int)

        
    return tempSeries

In [11]:
import pandas as pd

# # # Function to create aggregate features from list of features
# # # ### Function returns a Series
## -- df must be pandas dataframe where columns are
## -- inputList must be list of strings, where each string corresponds to a column name in df
def context_aggregator(df, inputList):
    
    aggSeries = df[inputList].sum(axis=1)
    
    return aggSeries

In [ ]:
# some non-linear transformations:
#sq -> df[i] ** 2
#log -> np.log(df[i] + 2)

## ¡Ojo! There are three spots in the function (generate_features_from_features) you would need to edit (and one spot where you change the "Type" string variable) to change the type of non-linear transformation used in the function

In [12]:
import pandas as pd
import numpy as np

# # # Function for generating new features for each feature in a list that you input
# # # ### Function returns a dataframe with all the new features concatenated
## -- df must be pandas dataframe where input features are stored
## -- featuresList must be list of strings of column names corresponding to input features you are targeting
## -- howFar must be an integer indicating how far from each token you want the context to be

def generate_features_from_features(df, featuresList, howFar):
    
    for i in featuresList:
        
        # Initialize empty lists for new window features that we will be generating 
        newFeaturesList = []
        NonLinear_newFeaturesList = []
        
        
        # +-+-+-+-+-+-+-+-+-+ Put in your own code for Non-Linear transformations! It's fun! +-+-+-+-+-+-+-+-+-+
        # ******* Type string for id of your non-linear transformation ********
        Type = "log"
        NonLinear_Feature = Type + "_" + i

        # ******* PUT CODE FOR NON LINEAR TRANSFORMATION HERE *******
        df[NonLinear_Feature] = np.log(df[i] + 2)
        
        
        
        # -----------------------------------------------------------------
        #------- Create window features and Non Linear Transformations of those window features
        for x in range(howFar):
            y = x + 1
            
            # -------------------------------- LEFT CONTEXT ----------------------------------
            newFeature = "L" + str(y) + "_" + i
            df[newFeature] = context_generator(df, i, contextDirection="left", contextDistance=y)
            
            # Add new feature to list
            newFeaturesList.append(newFeature)
            
            
            # +-+-+-+-+-+-+-+-+-+ Put in your own code for Non-Linear transformations! It's fun! +-+-+-+-+-+-+-+-+-+
            NonLinear_newFeature = Type + "_" + newFeature
            
            # ******* PUT CODE FOR NON LINEAR TRANSFORMATION HERE *******
            df[NonLinear_newFeature] = np.log(df[newFeature] + 2)
            
            # add each new Non-Linear Feature to a list
            NonLinear_newFeaturesList.append(NonLinear_newFeature)
            
            
            # -------------------------------- RIGHT CONTEXT ----------------------------------
            newFeature = "R" + str(y) + "_" + i
            df[newFeature] = context_generator(df, i, contextDirection="right", contextDistance=y)
            
            # Add new feature to list
            newFeaturesList.append(newFeature)
            
            
            # +-+-+-+-+-+-+-+-+-+ Put in your own code for Non-Linear transformations! It's fun! +-+-+-+-+-+-+-+-+-+
            NonLinear_newFeature = Type + "_" + newFeature
            
            # ******* PUT CODE FOR NON LINEAR TRANSFORMATION HERE *******
            df[NonLinear_newFeature] = np.log(df[newFeature] + 2)
            
            # add each new Non-Linear Feature to a list
            NonLinear_newFeaturesList.append(NonLinear_newFeature)
        
        
        
        # ------------------------------------------------------------ 
        # -------------- aggregate window features
        
        # Window range
        windowRange = howFar * 2 + 1
        
        # --------------------- For window features --------------------
        # Create name for column
        aggWindowFeature = "W" + str(windowRange) + "_" + i
        
        # Add column to dataframe, assigning it the series calculated by context_aggregator function
        df[aggWindowFeature] = context_aggregator(df, newFeaturesList)
        
        
        # ------------ For Non-Linear Transformations of Window Features ------------
        # Create name for column
        NL_aggWindowFeature = Type + "_" + aggWindowFeature
        
        # Add column to dataframe, assigning it the series calculated by context_aggregator function
        df[NL_aggWindowFeature] = context_aggregator(df, NonLinear_newFeaturesList)
        
    return df

In [6]:
import sklearn
#Import Gaussian Naive Bayes model
from sklearn.naive_bayes import GaussianNB
# import mean()
from statistics import mean
from sklearn.metrics import classification_report

def NB_loop(X, Y, pct, iterations):
    # label names
    target_names = ['Easy', 'Difficult']
    
    # make empty lists for p and f1 scores
#     precision_list_nb = []
#     recall_list_nb = []
#     f1_list_nb = []
#     ez_precision_list_nb = []
#     ez_recall_list_nb = []
#     ez_f1_list_nb = []
    
    for x in range(iterations):
        trainX, testX, trainY, testY = sklearn.model_selection.train_test_split(X,Y, test_size = pct)
        
        #Create a Gaussian Classifier
        model = GaussianNB()

        # Train the model using the training sets
        model.fit(trainX,trainY)

        #Predict Output
        Y_Bayes = model.predict(testX)
        
    return print(classification_report(testY, Y_Bayes, target_names=target_names))
        
        # Get precision score and f1 score, and append to list
#         p_nb = sklearn.metrics.precision_score(testY, Y_Bayes, labels=['Difficult'], pos_label=1)
#         precision_list_nb.append(p_nb)
        
#         r_nb = sklearn.metrics.recall_score(testY, Y_Bayes, labels=['Difficult'], pos_label=1)
#         recall_list_nb.append(r_nb)
        
#         f1_nb = sklearn.metrics.f1_score(testY, Y_Bayes, labels=['Difficult'], pos_label=1)
#         f1_list_nb.append(f1_nb)
        
#         ez_p_nb = sklearn.metrics.precision_score(testY, Y_Bayes, labels=['Easy'], pos_label=1)
#         ez_precision_list_nb.append(ez_p_nb)
        
#         ez_r_nb = sklearn.metrics.recall_score(testY, Y_Bayes, labels=['Easy'], pos_label=1)
#         ez_recall_list_nb.append(ez_r_nb)
        
#         ez_f1_nb = sklearn.metrics.f1_score(testY, Y_Bayes, labels=['Easy'], pos_label=1)
#         ez_f1_list_nb.append(ez_f1_nb)
        
#     # now return stuff in dict
#     mP_nb = mean(precision_list_nb)
#     mR_nb = mean(recall_list_nb)
#     mF1_nb = mean(f1_list_nb)
#     mP_X_mF1_nb = mP_nb * mF1_nb
#     ez_mP_nb = mean(ez_precision_list_nb)
#     ez_mR_nb = mean(ez_recall_list_nb)
#     ez_mF1_nb = mean(ez_f1_list_nb)
#     ez_mP_X_mF1_nb = ez_mP_nb * ez_mF1_nb
#     return {
#         "Difficult avg_precision": mP_nb,
#         "Difficult avg_recall": mR_nb,
#         "Difficult avg_f1": mF1_nb,
#         "Difficult Prec. * F1": mP_X_mF1_nb,
#         "Easy avg_precision": ez_mP_nb,
#         "Easy avg_recall": ez_mR_nb,
#         "Easy avg_f1": ez_mF1_nb,
#         "Easy Prec. * F1": ez_mP_X_mF1_nb
#     }
        

In [13]:
import sklearn
# Import the model we are using
from sklearn.ensemble import RandomForestClassifier
# import mean()
from statistics import mean

def RF_loop(X, Y, pct, iterations, trees):
    # label names
    target_names = ['Easy', 'Difficult']
    
    # make empty lists for p and f1 scores
#     precision_list_rf = []
#     recall_list_rf = []
#     f1_list_rf = []
    
    for x in range(iterations):
        trainX, testX, trainY, testY = sklearn.model_selection.train_test_split(X,Y, test_size = pct)
        
        # Instantiate model with 1000 decision trees
        rf = RandomForestClassifier(n_estimators = trees, random_state = 42)

        # Train the model on training data
        rf.fit(trainX, trainY);
        
        # Use the forest's predict method on the test data
        Y_rf = rf.predict(testX)
        
    return print(classification_report(testY, Y_rf, target_names=target_names))
        
        # Get precision score and f1 score, and append to list
#         p_rf = sklearn.metrics.precision_score(testY, Y_rf, labels=['Difficult'], pos_label=1)
#         precision_list_rf.append(p_rf)
        
#         r_rf = sklearn.metrics.recall_score(testY, Y_rf, labels=['Difficult'], pos_label=1)
#         recall_list_rf.append(r_rf)
        
#         f1_rf = sklearn.metrics.f1_score(testY, Y_rf, labels=['Difficult'], pos_label=1)
#         f1_list_rf.append(f1_rf)
        
#     # now return stuff in dict
#     mP_rf = mean(precision_list_rf)
#     mR_rf = mean(recall_list_rf)
#     mF1_rf = mean(f1_list_rf)
#     mP_X_mF1_rf = mP_rf * mF1_rf
#     return {
#         "avg_precision": mP_rf,
#         "avg_recall": mR_rf,
#         "avg_f1": mF1_rf,
#         "Prec. * F1": mP_X_mF1_rf
#     }
        

In [8]:
### import sklearn
#Import svm model
from sklearn import svm
# import mean()
from statistics import mean

def SVM_loop(X, Y, pct, iterations):
    # label names
    target_names = ['Easy', 'Difficult']
    
    # make empty lists for p and f1 scores
#     precision_list_svm = []
#     recall_list_svm = []
#     f1_list_svm = []
    
    for x in range(iterations):
        trainX, testX, trainY, testY = sklearn.model_selection.train_test_split(X,Y, test_size = pct)
        
        #Create a svm Classifier
        #clf = svm.SVC(kernel='linear') # Linear Kernel
        clf = svm.SVC(decision_function_shape='ovo', zero_division = )
        #clf = svm.LinearSVC()

        #Train the model using the training sets
        clf.fit(trainX, trainY)

        #Predict the response for test dataset
        Y_clf = clf.predict(testX)
        
    return print(classification_report(testY, Y_clf, target_names=target_names))
        
        # Get precision score and f1 score, and append to list
#         p_svm = sklearn.metrics.precision_score(testY, Y_clf, labels=['Difficult'], pos_label=1)
#         precision_list_svm.append(p_svm)
        
#         r_svm = sklearn.metrics.recall_score(testY, Y_clf, labels=['Difficult'], pos_label=1)
#         recall_list_svm.append(r_svm)
        
#         f1_svm = sklearn.metrics.f1_score(testY, Y_clf, labels=['Difficult'], pos_label=1)
#         f1_list_svm.append(f1_svm)
        
#     # now return stuff in dict
#     mP_svm = mean(precision_list_svm)
#     mR_svm = mean(recall_list_svm)
#     mF1_svm = mean(f1_list_svm)
#     mP_X_mF1_svm = mP_svm * mF1_svm
#     return {
#         "avg_precision": mP_svm,
#         "avg_recall": mR_svm,
#         "avg_f1": mF1_svm,
#         "Prec. * F1": mP_X_mF1_svm
#     }
        